# Übung 1: Finanz-PDF-Analyse mit RetrievalQA

In dieser Übung erstellen wir ein Q&A-System für einen Finanz- oder Risikobericht. Wir werden:
1. Einen PDF-Bericht laden
2. Den Text in Chunks aufteilen
3. Embeddings erstellen und in einem Vektorstore speichern
4. Eine RetrievalQA-Chain implementieren
5. Fragen an den Bericht stellen

## 1. Bibliotheken importieren

In [ ]:
import os
import time
from dotenv import load_dotenv

from langchain_community.document_loaders import PyPDFLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_openai import OpenAIEmbeddings
from langchain_community.vectorstores import Chroma
from langchain_openai import ChatOpenAI
from langchain.chains import RetrievalQA
from langchain.prompts import PromptTemplate

# Laden der Umgebungsvariablen (.env Datei mit OPENAI_API_KEY=sk-...)
load_dotenv()

# Alternativ API-Key direkt setzen
# os.environ["OPENAI_API_KEY"] = "sk-..."

## 2. PDF-Dokument laden

In [ ]:
# Pfad zum PDF-Dokument (passen Sie diesen an)
pdf_path = "pfad/zum/finanzbericht.pdf"

# PDF laden
loader = PyPDFLoader(pdf_path)
documents = loader.load()

print(f"Dokument geladen: {len(documents)} Seiten")

## 3. Text in Chunks aufteilen

In [ ]:
# Text Splitter konfigurieren
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=1000,  # Anzahl der Zeichen pro Chunk
    chunk_overlap=200,  # Überlappung zwischen Chunks
    length_function=len,
)

# Dokumente in Chunks aufteilen
chunks = text_splitter.split_documents(documents)

print(f"Dokument in {len(chunks)} Chunks aufgeteilt")

# Beispiel für einen Chunk anzeigen
print("\nBeispiel-Chunk:")
print(chunks[0].page_content[:200] + "...")

## 4. Embeddings erstellen und in Vektorstore speichern

In [ ]:
# Embeddings-Modell initialisieren
embeddings = OpenAIEmbeddings()

# Vektorstore erstellen
vectorstore = Chroma.from_documents(
    documents=chunks,
    embedding=embeddings,
    persist_directory="./chroma_db"  # Optional: Speichern der Vektoren auf Festplatte
)

print("Embeddings erstellt und in Vektorstore gespeichert")

## 5. RetrievalQA-Chain implementieren

In [ ]:
# LLM initialisieren
llm = ChatOpenAI(temperature=0, model="gpt-3.5-turbo")

# Angepasster Prompt für Finanzberichte
template = """
Du bist ein Finanzexperte, der Berichte analysiert. 
Verwende die folgenden Informationen, um die Frage zu beantworten.

Kontext:
{context}

Frage: {question}

Deine Antwort sollte:
1. Präzise und faktenbasiert sein
2. Relevante Kennzahlen hervorheben
3. Risiken klar benennen
4. Keine Informationen erfinden

Antwort:
"""

PROMPT = PromptTemplate(
    template=template,
    input_variables=["context", "question"]
)

# RetrievalQA-Chain erstellen
qa_chain = RetrievalQA.from_chain_type(
    llm=llm,
    chain_type="stuff",
    retriever=vectorstore.as_retriever(search_kwargs={"k": 4}),
    chain_type_kwargs={"prompt": PROMPT},
    return_source_documents=True  # Optional: Quellen zurückgeben
)

print("RetrievalQA-Chain erstellt")

## 6. Fragen an den Bericht stellen

In [ ]:
# Funktion zum Stellen von Fragen
def ask_question(question):
    start_time = time.time()
    result = qa_chain({"query": question})
    end_time = time.time()
    
    print(f"Frage: {question}")
    print(f"\nAntwort: {result['result']}")
    print(f"\nVerarbeitungszeit: {end_time - start_time:.2f} Sekunden")
    
    # Quellen anzeigen
    print("\nQuellen:")
    for i, doc in enumerate(result["source_documents"]):
        print(f"Quelle {i+1}: Seite {doc.metadata.get('page', 'unbekannt')}")
        print(f"Ausschnitt: {doc.page_content[:150]}...\n")

In [ ]:
# Beispielfragen
fragen = [
    "Was sind die größten Risikofaktoren laut Bericht?",
    "Wie hat sich die Eigenkapitalquote entwickelt?",
    "Welche ESG-Maßnahmen wurden umgesetzt?"
]

# Erste Frage stellen
ask_question(fragen[0])

In [ ]:
# Zweite Frage stellen
ask_question(fragen[1])

In [ ]:
# Dritte Frage stellen
ask_question(fragen[2])

## 7. Eigene Fragen stellen

Stellen Sie Ihre eigenen Fragen an den Bericht:

In [ ]:
# Eigene Frage
eigene_frage = "Wie hat sich der Cashflow im letzten Jahr entwickelt?"
ask_question(eigene_frage)

## 8. Reflexion

Beantworten Sie folgende Fragen:

1. Wie zufrieden sind Sie mit den Antworten?
2. Welche Verbesserungen könnten Sie vornehmen?
3. Wie könnte dieses System in Ihrem Arbeitsbereich eingesetzt werden?